# <center>Implementing LDA in Python</center>

<center>Dr. W.J.B. Mattingly</center>

<center>Smithsonian Data Science Lab and United States Holocaust Memorial Museum</center>

<center>February 2021</center>

## Key Concepts in this Notebook

## Introduction

## Importing the Required Libraries

In [1]:
#https://www.machinelearningplus.com/nlp/topic-modeling-gensim-python/#1introduction
import numpy as np
import json
import glob

#Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

#spacy
import spacy
from nltk.corpus import stopwords

#vis
import pyLDAvis
import pyLDAvis.gensim_models

import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)

In [2]:
%connect_info

{
  "shell_port": 54051,
  "iopub_port": 54052,
  "stdin_port": 54053,
  "control_port": 54055,
  "hb_port": 54054,
  "ip": "127.0.0.1",
  "key": "2a160da8-62eb3298254273683d4eccee",
  "transport": "tcp",
  "signature_scheme": "hmac-sha256",
  "kernel_name": ""
}

Paste the above JSON into a file, and connect with:
    $> jupyter <app> --existing <file>
or, if you are local, you can connect with just:
    $> jupyter <app> --existing kernel-16bf8a2e-ecf1-417c-8564-cb49042948d4.json
or even just:
    $> jupyter <app> --existing
if this is the most recent Jupyter kernel you have started.


## Preparing the Data

In [3]:
def load_data(file):
    with open (file, "r", encoding="utf-8") as f:
        data = json.load(f) 
    return (data)

def write_data(file, data):
    with open (file, "w", encoding="utf-8") as f:
        json.dump(data, f, indent=4)


In [4]:
stopwords = stopwords.words("english")

In [5]:
print (stopwords)

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

In [6]:
data = load_data("data/ushmm_dn.json")["texts"]

print (data[0][0:90])

 My name David Kochalski. I was born in a small town called , and I was born May 5, 1928. 


In [7]:
def lemmatization(texts, allowed_postags=["NOUN", "ADJ", "VERB", "ADV"]):
    nlp = spacy.load("en_core_web_sm", disable=["parser", "ner"])
    texts_out = []
    for text in texts:
        doc = nlp(text)
        new_text = []
        for token in doc:
            if token.pos_ in allowed_postags:
                new_text.append(token.lemma_)
        final = " ".join(new_text)
        texts_out.append(final)
    return (texts_out)


lemmatized_texts = lemmatization(data)
print (lemmatized_texts[0][0:90])

name bear small town call bear well very hard work child father mother small mill flour bu


In [8]:
def gen_words(texts):
    final = []
    for text in texts:
        new = gensim.utils.simple_preprocess(text, deacc=True)
        final.append(new)
    return (final)

data_words = gen_words(lemmatized_texts)

print (data_words[0][0:20])

['name', 'bear', 'small', 'town', 'call', 'bear', 'well', 'very', 'hard', 'work', 'child', 'father', 'mother', 'small', 'mill', 'flour', 'buckwheat', 'prosperous', 'comfortable', 'go']


In [50]:
id2word = corpora.Dictionary(data_words)

corpus = []
for text in data_words:
    new = id2word.doc2bow(text)
    corpus.append(new)

print (corpus[0][0:20])

word = id2word[[0][:1][0]]
print (word)

[(0, 2), (1, 10), (2, 1), (3, 2), (4, 1), (5, 2), (6, 1), (7, 2), (8, 3), (9, 1), (10, 12), (11, 1), (12, 8), (13, 1), (14, 2), (15, 1), (16, 3), (17, 2), (18, 1), (19, 2)]
able


In [54]:
corpus

[[(0, 2),
  (1, 10),
  (2, 1),
  (3, 2),
  (4, 1),
  (5, 2),
  (6, 1),
  (7, 2),
  (8, 3),
  (9, 1),
  (10, 12),
  (11, 1),
  (12, 8),
  (13, 1),
  (14, 2),
  (15, 1),
  (16, 3),
  (17, 2),
  (18, 1),
  (19, 2),
  (20, 1),
  (21, 8),
  (22, 10),
  (23, 1),
  (24, 7),
  (25, 16),
  (26, 10),
  (27, 5),
  (28, 2),
  (29, 1),
  (30, 1),
  (31, 1),
  (32, 2),
  (33, 1),
  (34, 3),
  (35, 2),
  (36, 2),
  (37, 3),
  (38, 2),
  (39, 1),
  (40, 1),
  (41, 4),
  (42, 1),
  (43, 1),
  (44, 1),
  (45, 11),
  (46, 1),
  (47, 1),
  (48, 4),
  (49, 4),
  (50, 8),
  (51, 2),
  (52, 1),
  (53, 8),
  (54, 2),
  (55, 1),
  (56, 21),
  (57, 1),
  (58, 1),
  (59, 1),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 2),
  (64, 12),
  (65, 10),
  (66, 27),
  (67, 22),
  (68, 2),
  (69, 1),
  (70, 7),
  (71, 1),
  (72, 2),
  (73, 1),
  (74, 1),
  (75, 6),
  (76, 3),
  (77, 1),
  (78, 4),
  (79, 1),
  (80, 2),
  (81, 2),
  (82, 2),
  (83, 5),
  (84, 1),
  (85, 4),
  (86, 1),
  (87, 1),
  (88, 3),
  (89, 11),
  (90, 2

In [55]:
lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=30,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha="auto")


## Vizualizing the Data

In [56]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim_models.prepare(lda_model, corpus, id2word, mds="mmds", R=30)
vis

C:\Users\KARTIKS\Anaconda3\envs\pytorch38\lib\site-packages\pyLDAvis\_prepare.py:246: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
15     0.322458  0.262356       1        1  24.294838
29     0.281475  0.086779       2        1  21.622457
8      0.384958  0.228867       3        1  12.215752
17     0.328272  0.201019       4        1  11.824005
14     0.358065  0.130655       5        1  11.011981
25     0.391259  0.064278       6        1   9.658179
20     0.302212  0.350143       7        1   7.791218
3      0.417633 -0.121595       8        1   1.417060
18     0.040416 -0.248443       9        1   0.154251
19    -0.146701 -0.033636      10        1   0.004538
2     -0.133988 -0.046015      11        1   0.000306
28    -0.133995 -0.046018      12        1   0.000301
26    -0.133993 -0.046017      13        1   0.000299
9     -0.133998 -0.046019      14        1   0.000298
24    -0.133998 -0.046019      15        1   0.000297
10    -0.133999 -0.046020      16        1   0.000296
1     -0.134000 -0.046020      17        1   0.000296
23    -0.133999 -0.046020      18        1   0.000294
13    -0.134003 -0.046021      19        1   0.000293
0     -0.134004 -0.046022      20        1   0.000283
21    -0.134005 -0.046022      21        1   0.000282
4     -0.134006 -0.046023      22        1   0.000280
6     -0.134006 -0.046023      23        1   0.000278
5     -0.134006 -0.046023      24        1   0.000277
16    -0.134006 -0.046023      25        1   0.000277
12    -0.134006 -0.046023      26        1   0.000277
7     -0.134007 -0.046023      27        1   0.000274
22    -0.134008 -0.046024      28        1   0.000272
11    -0.134008 -0.046024      29        1   0.000271
27    -0.134009 -0.046024      30        1   0.000271, topic_info=       Term         Freq        Total Category  logprob  loglift
683     run  2343.000000  2343.000000  Default  30.0000  30.0000
892    year  3466.000000  3466.000000  Default  29.0000  29.0000
152   child  3170.000000  3170.000000  Default  28.0000  28.0000
133    camp  4522.000000  4522.000000  Default  27.0000  27.0000
803   think  5635.000000  5635.000000  Default  26.0000  26.0000
..      ...          ...          ...      ...      ...      ...
643  really     0.000165  3247.677603  Topic30  -9.6434  -3.9795
485    make     0.000165  5070.539570  Topic30  -9.6434  -4.4251
758   start     0.000165  3697.038284  Topic30  -9.6434  -4.1092
859     war     0.000165  3085.747999  Topic30  -9.6434  -3.9285
498    mean     0.000165  2910.151412  Topic30  -9.6435  -3.8699

[3060 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
5647      2  0.981723  academic
904       1  0.080228    accept
904       2  0.649116    accept
904       3  0.003647    accept
904       4  0.113048    accept
...     ...       ...       ...
892       9  0.006634      year
3960      2  0.080578     zloty
3960      3  0.859500     zloty
3960      4  0.080578     zloty
8529      9  0.905719      zoom

[2225 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[16, 30, 9, 18, 15, 26, 21, 4, 19, 20, 3, 29, 27, 10, 25, 11, 2, 24, 14, 1, 22, 5, 7, 6, 17, 13, 8, 23, 12, 28])